In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
import pickle
from embedding import *
import warnings
warnings.filterwarnings('ignore')

In [3]:
with open('../Data/random_samples.pkl', 'rb') as f:
    random_samples = pickle.load(f)

In [4]:
with open('../Data/random_samples_bon_spoof.pkl', 'rb') as f:
    random_samples_bon_spoof = pickle.load(f)

In [9]:
mfccs_mean,cqccs_mean=preprocess_audio_samples(random_samples,with_compute=True,mean=True)

Preprocessing Audio: 100%|████████████████████| 1950/1950 [28:24<00:00,  1.14samples/s]


In [12]:
mfccs_mean_spoof_bonafide,cqccs_mean_spoof_bonafide=preprocess_audio_samples(random_samples_bon_spoof,with_compute=True,mean=True)


Preprocessing Audio: 100%|████████████████████| 1950/1950 [25:58<00:00,  1.25samples/s]


In [13]:
mfccs_mean_std,cqccs_mean_std=preprocess_audio_samples(random_samples,with_compute=True,mean=True,variance=True)


Preprocessing Audio: 100%|████████████████████| 1950/1950 [39:34<00:00,  1.22s/samples]


In [14]:
mfccs_mean_std_spoof_bonafide,cqccs_mean_std_spoof_bonafide=preprocess_audio_samples(random_samples_bon_spoof,with_compute=True,mean=True,variance=True)


Preprocessing Audio: 100%|████████████████████| 1950/1950 [25:55<00:00,  1.25samples/s]


In [15]:
mfccs_mean_std_avg,cqccs_mean_std_avg=preprocess_audio_samples(random_samples,with_compute=True,mean=True,variance=True,avg_diff=True)


Preprocessing Audio: 100%|████████████████████| 1950/1950 [20:21<00:00,  1.60samples/s]


In [16]:
mfccs_mean_std_avg_spoof_bonafide,cqccs_mean_std_avg_spoof_bonafide=preprocess_audio_samples(random_samples_bon_spoof,with_compute=True,mean=True,variance=True,avg_diff=True)


Preprocessing Audio: 100%|████████████████████| 1950/1950 [20:29<00:00,  1.59samples/s]


In [28]:
wlxvector_embedding=wlXvector_embedding(random_samples_bon_spoof)



Preprocessing Audio:   0%|                    | 0/1950 [00:00<?, ?samples/s]Some weights of the model checkpoint at microsoft/wavlm-base-plus-sv were not used when initializing WavLMForXVector: ['wavlm.encoder.pos_conv_embed.conv.weight_g', 'wavlm.encoder.pos_conv_embed.conv.weight_v']
- This IS expected if you are initializing WavLMForXVector from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing WavLMForXVector from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of WavLMForXVector were not initialized from the model checkpoint at microsoft/wavlm-base-plus-sv and are newly initialized: ['wavlm.encoder.pos_conv_embed.conv.parametrizations.weight.original0', 'wavlm.encoder.pos_conv_embed.conv.p

In [48]:
wlxvector_embedding["bonafide"]=wlxvector_embedding["bonafide"].reshape(-1,512)
wlxvector_embedding["spoof"]=wlxvector_embedding["spoof"].reshape(-1,512)

In [31]:
unispeechsat_embedding=uniSpeechSat_embedding(random_samples_bon_spoof)

Preprocessing Audio:   0%|                    | 0/1950 [00:00<?, ?samples/s]

preprocessor_config.json:   0%|          | 0.00/213 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/58.1k [00:00<?, ?B/s]

pytorch_model.bin:   0%|          | 0.00/404M [00:00<?, ?B/s]

Some weights of the model checkpoint at microsoft/unispeech-sat-base-plus-sv were not used when initializing UniSpeechSatForXVector: ['unispeech_sat.encoder.pos_conv_embed.conv.weight_g', 'unispeech_sat.encoder.pos_conv_embed.conv.weight_v']
- This IS expected if you are initializing UniSpeechSatForXVector from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing UniSpeechSatForXVector from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of UniSpeechSatForXVector were not initialized from the model checkpoint at microsoft/unispeech-sat-base-plus-sv and are newly initialized: ['unispeech_sat.encoder.pos_conv_embed.conv.parametrizations.weight.original0', 'unispeech_sat.encoder.pos_conv_embed.conv.par

In [49]:
unispeechsat_embedding["bonafide"]=unispeechsat_embedding["bonafide"].reshape(-1,512)
unispeechsat_embedding["spoof"]=unispeechsat_embedding["spoof"].reshape(-1,512)

In [33]:
cqcc_mfccs_fusion={}
cqcc_mfccs_fusion["bonafide"]=np.append(mfccs_mean_std_spoof_bonafide["bonafide"]
                                        ,cqccs_mean_std_spoof_bonafide["bonafide"],axis=1)
cqcc_mfccs_fusion["spoof"]=np.append(mfccs_mean_std_spoof_bonafide["spoof"]
                                        ,cqccs_mean_std_spoof_bonafide["spoof"],axis=1)

In [ ]:
mfccs,cqccs=preprocess_audio_samples(random_samples_bon_spoof,with_compute=False)

In [11]:
def save_embeddings_to_tsv(embeddings, output_dir):
    total_samples = len(embeddings.keys())
    progress_bar = tqdm(total=total_samples, desc=f"Saving tsv Files", unit="files")
    for filename, embedding_data in embeddings.items():
        output_file = os.path.join(output_dir, filename + ".tsv")
        metadata_file = os.path.join(output_dir, filename + "_metadata.tsv")  # Metadata file path

        with open(output_file, 'w') as f, open(metadata_file, 'w') as meta_f:  # Open metadata file

            for label, embedding_samples in embedding_data.items():
                for embedding in embedding_samples:
                    embedding_str = '\t'.join([str(e) for e in embedding])
                    f.write(f"{embedding_str}\n")
                    meta_f.write(f"{label}\n")

        progress_bar.update(1)
    progress_bar.close()

In [12]:
output_dir = "../Data/embedding_files"
embedding_files = {
    "mfccs":mfccs,
    "cqccs":cqccs
    # "mfccs_mean": mfccs_mean,
    # "cqccs_mean": cqccs_mean,
    # "mfccs_mean_std": mfccs_mean_std,
    # "cqccs_mean_std": cqccs_mean_std,
    # "mfccs_mean_std_avg": mfccs_mean_std_avg,
    # "cqccs_mean_std_avg": cqccs_mean_std_avg,
    # "mfccs_mean_spoof_bonafide": mfccs_mean_spoof_bonafide,
    # "cqccs_mean_spoof_bonafide": cqccs_mean_spoof_bonafide,
    # "mfccs_mean_std_spoof_bonafide": mfccs_mean_std_spoof_bonafide,
    # "cqccs_mean_std_spoof_bonafide": cqccs_mean_std_spoof_bonafide,
    # "mfccs_mean_std_avg_spoof_bonafide": mfccs_mean_std_avg_spoof_bonafide,
    # "cqccs_mean_std_avg_spoof_bonafide": cqccs_mean_std_avg_spoof_bonafide,
    # "cqcc_mfccs_fusion":cqcc_mfccs_fusion,
    # "unispeechsat_embedding":unispeechsat_embedding,
    # "wlxvector_embedding":wlxvector_embedding
}
os.makedirs(output_dir, exist_ok=True)
save_embeddings_to_tsv(embedding_files, output_dir)

Saving tsv Files: 100%|██████████| 2/2 [01:24<00:00, 42.01s/files]


In [52]:
evaluation_feats={
    "mfccs_mean_spoof_bonafide": mfccs_mean_spoof_bonafide,
    "cqccs_mean_spoof_bonafide": cqccs_mean_spoof_bonafide,
    "mfccs_mean_std_spoof_bonafide": mfccs_mean_std_spoof_bonafide,
    "cqccs_mean_std_spoof_bonafide": cqccs_mean_std_spoof_bonafide,
    "mfccs_mean_std_avg_spoof_bonafide": mfccs_mean_std_avg_spoof_bonafide,
    "cqccs_mean_std_avg_spoof_bonafide": cqccs_mean_std_avg_spoof_bonafide,
    "cqcc_mfccs_fusion":cqcc_mfccs_fusion,
    "unispeechsat_embedding":unispeechsat_embedding,
    "wlxvector_embedding":wlxvector_embedding
                   }

In [13]:
from sklearn.cluster import KMeans
from sklearn.metrics import silhouette_score
import time
def get_silhouette_score(feats):
    X=np.append(feats["bonafide"],feats["spoof"],axis=0)
    print(X.shape)
    kmeans = KMeans(n_clusters=2, random_state=42)
    return silhouette_score(X, kmeans.fit_predict(X))
def compute_evaluation_score(evaluation_feats):
    scores = {}
    computation_times = {}
    total_samples =len(evaluation_feats.keys())
    progress_bar = tqdm(total=total_samples, bar_format='{l_bar}{bar:20}{r_bar}',
                        desc=f"Evaluating Audio Features",
                        unit="Features")
    for feat_name, feats in evaluation_feats.items():
        start_time = time.time()
        scores[feat_name] = get_silhouette_score(feats)
        end_time = time.time()
        computation_times[feat_name] = end_time - start_time
        progress_bar.update(1)
    evaluation_df = pd.DataFrame({
    'Feature Extraction Technique': list(scores.keys()),
    'Silhouette Score': list(scores.values()),
    'Computation Time (seconds)': list(computation_times.values())
})
    progress_bar.close()
    return evaluation_df

In [57]:
evaluation_data=compute_evaluation_score(evaluation_feats)     


Evaluating Audio Features:   0%|                    | 0/9 [00:00<?, ?Features/s]

(1950, 80)



Evaluating Audio Features:  11%|██▏                 | 1/9 [00:00<00:02,  2.87Features/s]

(1950, 120)



Evaluating Audio Features:  22%|████▍               | 2/9 [00:00<00:02,  3.13Features/s]

...


Evaluating Audio Features:  78%|███████████████▌    | 7/9 [00:02<00:00,  3.41Features/s]

(1950, 512)



Evaluating Audio Features:  89%|█████████████████▊  | 8/9 [00:02<00:00,  2.78Features/s]

(1950, 512)



Evaluating Audio Features: 100%|████████████████████| 9/9 [00:03<00:00,  2.86Features/s]


In [58]:
evaluation_data

Feature Extraction Technique  Silhouette Score  \
0          mfccs_mean_spoof_bonafide          0.140051   
1          cqccs_mean_spoof_bonafide          0.628916   
2      mfccs_mean_std_spoof_bonafide          0.140051   
3      cqccs_mean_std_spoof_bonafide          0.628916   
4  mfccs_mean_std_avg_spoof_bonafide          0.138450   
5  cqccs_mean_std_avg_spoof_bonafide          0.621398   
6                  cqcc_mfccs_fusion          0.125858   
7             unispeechsat_embedding          0.323214   
8                wlxvector_embedding          0.287372   

   Computation Time (seconds)  
0                    0.348095  
1                    0.289662  
2                    0.266359  
3                    0.234373  
4                    0.295573  
5                    0.298179  
6                    0.296875  
7                    0.487236  
8                    0.562033

In [59]:
evaluation_data.to_csv('../Data/evaluation.csv',index=False)

In [14]:
ev=compute_evaluation_score(embedding_files)

Evaluating Audio Features:   0%|                    | 0/2 [00:00<?, ?Features/s]

(1950, 14040)


Evaluating Audio Features:  50%|██████████          | 1/2 [04:26<04:26, 266.64s/Features]

(1950, 14040)


Evaluating Audio Features: 100%|████████████████████| 2/2 [07:00<00:00, 210.35s/Features]


In [16]:
ev.to_csv('ev.csv',index=False)